In [ ]:
# Install vLLM
!pip install -q vllm

# Ensure spawn is used before importing vLLM
import multiprocessing as mp
mp.set_start_method("spawn", force=True)

# Import libraries
import pandas as pd
from vllm import LLM, SamplingParams


   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 438.2/438.2 MB 2.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 180.0/180.0 kB 18.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.5/45.5 kB 5.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 111.0/111.0 kB 14.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 45.4/45.4 kB 5.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.9/3.9 MB 71.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 108.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 117.2/117.2 MB 18.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.7/8.7 MB 128.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 96.2/96.2 kB 12.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 15.0/15.0 MB 133.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.5/6.5 MB 95.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.0/3.0 

In [ ]:

# Load your CSV
# # Replace 'your_data.csv' with your file path
# df = pd.read_csv("/content/your_data.csv")
# # Replace 'text' with the column containing URLs or email/text data
# texts = df["text"].astype(str).tolist()

# Mount Google Drive
from google.colab import drive
drive.mount('/content/drive')
path = "/content/drive/MyDrive/fraud_group_project/dataset_phishing.csv"
df = pd.read_csv(path)
texts = df["url"].astype(str).tolist()


Mounted at /content/drive


In [ ]:
len(texts)

In [ ]:

# Initialize vLLM model
llm = LLM(
    model="Qwen/Qwen2.5-7B-Instruct",
    dtype="bfloat16",          # GPU-friendly on Colab T4/A100
    trust_remote_code=True
)



INFO 11-18 12:57:18 [utils.py:233] non-default args: {'trust_remote_code': True, 'dtype': 'bfloat16', 'disable_log_stats': True, 'model': 'Qwen/Qwen2.5-7B-Instruct'}


The argument `trust_remote_code` is to be used with Auto classes. It has no effect here and is ignored.
/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/663 [00:00<?, ?B/s]

INFO 11-18 12:57:40 [model.py:547] Resolved architecture: Qwen2ForCausalLM


`torch_dtype` is deprecated! Use `dtype` instead!


...

vocab.json: 0.00B [00:00, ?B/s]

merges.txt: 0.00B [00:00, ?B/s]

tokenizer.json: 0.00B [00:00, ?B/s]

generation_config.json:   0%|          | 0.00/243 [00:00<?, ?B/s]

WARNING 11-18 12:57:49 [__init__.py:3036] We must use the `spawn` multiprocessing start method. Overriding VLLM_WORKER_MULTIPROC_METHOD to 'spawn'. See https://docs.vllm.ai/en/latest/usage/troubleshooting.html#python-multiprocessing for more information. Reasons: CUDA is initialized
INFO 11-18 13:00:07 [llm.py:306] Supported_tasks: ['generate']


In [4]:

# Sampling parameters: deterministic
sampling_params = SamplingParams(
    temperature=0.0,
    # max_tokens=50,
    max_tokens = 100,
    stop = ["}"],
    include_stop_str_in_output = True
    # stop=["```json"],
    # response_format=json
)

In [5]:
# def build_prompt(url):
#     return f"""
# Analyze the potential phishing URL below and describe suspicious features.
# URL: {url}

# Output ONLY this JSON with the following fields, do not output anything else:
# {{
#   "contains_brand_misspell": "Boolean true or false",
#   "suspicious_words": "List of suspicious keywords found in the URL",
#   "risk_score": "Integer from 0 to 100 indicating phishing risk"
# }}

# """

def build_prompt(url):
    return f"""
You are a cybersecurity URL-analysis model. Analyze the URL below and extract phishing-related features.

URL: {url}

Definitions:
- A *brand misspell* occurs when a well-known brand name is intentionally modified (e.g., rnicrosoft instead of microsoft).
- A *homoglyph attack* occurs when one or more characters in a domain or brand name are replaced with visually similar characters to mimic a legitimate brand.
  Examples include:
    - Latin substitution: replacing letters with visually similar letters from the same alphabet (rn → m, l → I)
    - Cross-alphabet: replacing letters with visually similar letters from another alphabet (Cyrillic 'а' → Latin 'a')
    - Number/symbol substitution: using numbers or symbols (0 → O, 1 → l, @ → a)
    - Multi-character substitution: replacing one character with multiple characters (m → rn, w → vv)
    - Mixed: combining any of the above

Steps:
1) Read the URL given to you.
2) Identify embedded brand tokens (e.g., paypal, microsoft, google, amazon, apple).
3) Determine if the brand is:
     - **misspelled** (letter swaps/add/remove)
     - **homoglyph attack** (rn→m, l→1, Cyrillic a→Latin a, etc.)
4) If homoglyph attack → set "homoglyph_type" to one of:
     "latin", "cross-alphabet", "number-symbol", "multi-character", "mixed"
5) Assign a phishing "risk_score" from 0 to 100.
6) Output ONLY one final JSON object. Do NOT include explanations, comments, markdown, or text before/after the JSON.

Required JSON fields:
{{
  "contains_brand_misspell": true or false,
  "is_homoglyph_attack": true or false,
  "homoglyph_type": "latin | cross-alphabet | number-symbol | multi-character | mixed | none",
  "risk_score": integer from 0 to 100
}}

Rules:
- If no homoglyph attack is detected, set `"homoglyph_type": "none"`.
- `"risk_score"` should reflect overall phishing risk based only on the URL.
- Output must be valid JSON and nothing else.

Example 1:
Input URL: https://paypa1-secure-login.com/reset
Correct Output:
{{
  "contains_brand_misspell": false,
  "is_homoglyph_attack": true,
  "homoglyph_type": "number-symbol",
  "risk_score": 92
}}
"""



# sample_url = "https://huggingface.co/Qwen/Qwen2.5-7B-Instruct"
# sample_url = "https://www.rnicrosoft.com"
sample_url = "http://shadetreetechnology.com/V4/validation/a111aedc8ae390eabcfa130e041a10a4"
prompt = build_prompt(sample_url)
output = llm.generate(prompt, sampling_params)
print(output)


Adding requests:   0%|          | 0/1 [00:00<?, ?it/s]

Processed prompts:   0%|          | 0/1 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

[RequestOutput(request_id=0, prompt='\nYou are a cybersecurity URL-analysis model. Analyze the URL below and extract phishing-related features.\n\nURL: http://shadetreetechnology.com/V4/validation/a111aedc8ae390eabcfa130e041a10a4\n\nDefinitions:\n- A *brand misspell* occurs when a well-known brand name is intentionally modified (e.g., rnicrosoft instead of microsoft).\n- A *homoglyph attack* occurs when one or more characters in a domain or brand name are replaced with visually similar characters to mimic a legitimate brand.\n  Examples include:\n    - Latin substitution: replacing letters with visually similar letters from the same alphabet (rn → m, l → I)\n    - Cross-alphabet: replacing letters with visually similar letters from another alphabet (Cyrillic \'а\' → Latin \'a\')\n    - Number/symbol substitution: using numbers or symbols (0 → O, 1 → l, @ → a)\n    - Multi-character substitution: replacing one character with multiple characters (m → rn, w → vv)\n    - Mixed: combining a

In [8]:
import json
text_output = output[0].outputs[0].text
# print(text_output)
# json_output = json.loads(text_output)
# print(json_output)
print(safe_extract_json(text_output))

{'contains_brand_misspell': False, 'is_homoglyph_attack': False, 'homoglyph_type': 'none', 'risk_score': 20}


In [7]:
import json
import re

def safe_extract_json(text):
    """Extract only the first valid JSON object from LLM output."""
    match = re.search(r"\{.*?\}", text, re.DOTALL)
    if not match:
        return None
    try:
        return json.loads(match.group())
    except:
        return None


def classify_texts(texts, batch_size=32):
    predictions = []
    total = len(texts)
    # total = 32

    for i in range(0, total, batch_size):
        batch = texts[i:i+batch_size]
        prompts = [build_prompt(t) for t in batch]

        outputs = llm.generate(prompts, sampling_params)

        batch_preds = []
        for output in outputs:
            raw = output.outputs[0].text     # vLLM format
            parsed = safe_extract_json(raw)

            if parsed is None:
                parsed = {
                    "contains_brand_misspell": None,
                    "is_homoglyph_attack": None,
                    "homoglyph_type": '',
                    # "suspicious_words": [],
                    "risk_score": None
                }

            batch_preds.append(parsed)

        predictions.extend(batch_preds)
        print(f"Processed {len(predictions)}/{total} rows")

    return predictions


In [9]:
predictions = classify_texts(texts, batch_size=32)


Adding requests:   0%|          | 0/32 [00:00<?, ?it/s]

Processed prompts:   0%|          | 0/32 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Processed 32/11430 rows


Adding requests:   0%|          | 0/32 [00:00<?, ?it/s]

Processed prompts:   0%|          | 0/32 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

...

Processed prompts:   0%|          | 0/32 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Processed 11424/11430 rows


Adding requests:   0%|          | 0/6 [00:00<?, ?it/s]

Processed prompts:   0%|          | 0/6 [00:00<?, ?it/s, est. speed input: 0.00 toks/s, output: 0.00 toks/s]

Processed 11430/11430 rows


In [10]:
df["contains_brand_misspell"] = [
    p["contains_brand_misspell"] for p in predictions
]
df["is_homoglyph_attack"] = [
    p["is_homoglyph_attack"] for p in predictions
]
df["homoglyph_type"] = [
    p["homoglyph_type"] for p in predictions
]
# df["suspicious_words"] = [
#     ",".join(p["suspicious_words"]) for p in predictions
# ]
df["risk_score"] = [
    p["risk_score"] for p in predictions
]


In [11]:
df.head()

url  length_url  \
0              http://www.crestonwood.com/router.php          37   
1  http://shadetreetechnology.com/V4/validation/a...          77   
2  https://support-appleld.com.secureupdate.duila...         126   
3                                 http://rgipt.ac.in          18   
4  http://www.iracing.com/tracks/gateway-motorspo...          55   

   length_hostname  ip  nb_dots  nb_hyphens  nb_at  nb_qm  nb_and  nb_or  ...  \
0               19   0        3           0      0      0       0      0  ...   
1               23   1        1           0      0      0       0      0  ...   
2               50   1        4           1      0      1       2      0  ...   
3               11   0        2           0      0      0       0      0  ...   
4               15   0        2           2      0      0       0      0  ...   

   domain_age  web_traffic  dns_record  google_index  page_rank      status  \
0          -1            0           1             1          4  legitimate   
1        5767            0           0             1          2    phishing   
2        4004      5828815           0             1          0    phishing   
3          -1       107721           0             0          3  legitimate   
4        8175         8725           0             0          6  legitimate   

   contains_brand_misspell  is_homoglyph_attack  homoglyph_type  risk_score  
0                    False                False            none          10  
1                    False                False            none          20  
2                     True                 True           mixed          85  
3                    False                False            none          10  
4                    False                False            none          10  

[5 rows x 93 columns]

In [ ]:
df.iloc[1]["url"]

'http://shadetreetechnology.com/V4/validation/a111aedc8ae390eabcfa130e041a10a4'

In [ ]:
# count the number of none
df["contains_brand_misspell"].value_counts().sum()

np.int64(10413)

In [12]:
df.to_csv(
    "/content/drive/MyDrive/fraud_group_project/llm_engineered_dataset_new.csv",
    index=False
)

print("Classification complete! Saved to llm_engineered_dataset.csv")


Classification complete! Saved to llm_engineered_dataset.csv
